In [0]:
# 03_feature_engineering.py

from pyspark.sql.functions import col, avg, stddev, count, lit
from pyspark.sql.window import Window

CATALOG = "workspace"
SCHEMA  = "default"

silver_tbl = f"{CATALOG}.{SCHEMA}.stocks_silver"
gold_tbl   = f"{CATALOG}.{SCHEMA}.stocks_gold_features"

df_silver = spark.table(silver_tbl)

# Rolling windows; we use rowsBetween to compute trailing windows by row index
w7  = Window.partitionBy("symbol").orderBy("date").rowsBetween(-6, 0)
w14 = Window.partitionBy("symbol").orderBy("date").rowsBetween(-13, 0)
w30 = Window.partitionBy("symbol").orderBy("date").rowsBetween(-29, 0)

df_gold = (
    df_silver
      .withColumn("ma_7",   avg(col("close")).over(w7))
      .withColumn("ma_14",  avg(col("close")).over(w14))
      .withColumn("ma_30",  avg(col("close")).over(w30))
      .withColumn("vol_14", stddev(col("return")).over(w14))
      .withColumn("obs_count", count(lit(1)).over(w30))
)

(df_gold.write
    .format("delta")
    .mode("overwrite")
    .saveAsTable(gold_tbl))

display(spark.table(gold_tbl))

symbol date open high low close volume return ma_7 ma_14 ma_30 vol_14 obs_count A 2014-01-02 57.1 57.1 56.15 56.21 1916160 null 56.21 56.21 56.21 null 1 A 2014-01-03 56.39 57.345 56.26 56.92 1866651 0.012631204412026345 56.565 56.565 56.565 null 2 A 2014-01-06 57.4 57.7 56.56 56.64 1777472 -0.004919184820801144 56.589999999999996 56.589999999999996 56.589999999999996 0.012409999238995688 3 A 2014-01-07 56.95 57.63 56.93 57.45 1463208 0.014300847457627159 56.80499999999999 56.80499999999999 56.80499999999999 0.010647484138731992 4 A 2014-01-08 57.33 58.54 57.17 58.39 2659468 0.016362053959965147 57.12199999999999 57.12199999999999 57.12199999999999 0.009794864494323555 5 A 2014-01-09 58.4 58.68 57.87 58.41 1757647 3.425244048637784E-4 57.336666666666666 57.336666666666666 57.336666666666666 0.009437769321857466 6 A 2014-01-10 58.51 59.01 58.14 58.93 1623330 0.008902585173771668 57.56428571428571 57.56428571428571 57.56428571428571 0.008454650147075913 7 A 2014-01-13 58.77 59.1 58.6 58.93 2946738 0.0 57.952857142857134 57.735 57.735 0.008280475272508784 8 A 2014-01-14 59.16 59.95 59.02 59.88 2562236 0.016120821313422753 58.37571428571429 57.97333333333333 57.97333333333333 0.008344107864895246 9 A 2014-01-15 59.82 60.365 59.585 60.34 2335194 0.007682030728122927 58.90428571428572 58.21 58.21 0.007805778664232132 10 A 2014-01-16 60.24 60.5 60.04 60.5 1835957 0.0026516407026847297 59.339999999999996 58.41818181818182 58.41818181818182 0.007546686332428493 11 A 2014-01-17 60.83 60.83 60.33 60.71 1699534 0.0034710743801653035 59.67142857142857 58.609166666666674 58.609166666666674 0.00725712546354216 12 A 2014-01-21 60.69 60.88 59.86 60.85 3008458 0.0023060451325976044 60.02 58.78153846153847 58.78153846153847 0.00705359290464244 13 A 2014-01-22 60.82 61.22 60.71 60.93 2769350 0.00131470829909611 60.305714285714295 58.935 58.935 0.006913772510750832 14 A 2014-01-23 60.48 60.51 59.405 59.47 3063559 -0.02396192351879207 60.382857142857155 59.167857142857144 58.97066666666667 0.010454315162274182 15 A 2014-01-24 59.22 59.46 57.71 57.87 2656341 -0.02690432150664203 60.09571428571428 59.23571428571429 58.901875000000004 0.01299863930479674 16 A 2014-01-27 57.9 58.37 56.98 58.3 4669012 0.007430447554864347 59.80428571428572 59.354285714285716 58.866470588235295 0.012965894320865525 17 A 2014-01-28 58.5 58.88 57.91 58.1 2536290 -0.003430531732418452 59.46142857142858 59.40071428571428 58.82388888888889 0.012546292780411555 18 A 2014-01-29 57.67 58.2174 57.41 57.65 2163031 -0.0077452667814114085 59.02428571428572 59.347857142857144 58.7621052631579 0.011895052278194339 19 A 2014-01-30 58.42 60.11 58.42 59.51 3743153 0.03226366001734605 58.832857142857144 59.42642857142857 58.7995 0.014835884312236479 20 A 2014-01-31 58.61 59.15 58.05 58.15 3529054 -0.022853301966056117 58.435714285714276 59.37071428571428 58.768571428571434 0.01598922811216198 21 A 2014-02-03 58.15 58.48 56.075 56.15 2929252 -0.034393809114359415 57.96142857142856 59.17214285714285 58.64954545454546 0.018323364506789397 22 A 2014-02-04 56.32 57.88 56.09 57.81 2911877 0.029563668744434616 57.952857142857134 59.02428571428571 58.61304347826088 0.019717910596072287 23 A 2014-02-05 57.58 57.7 56.96 57.43 2283870 -0.006573257221933966 57.82857142857143 58.81642857142857 58.563750000000006 0.01952833439655748 24 A 2014-02-06 57.51 58.35 57.46 58.29 1609451 0.014974751871843973 57.855714285714285 58.65857142857142 58.552800000000005 0.020089199885126474 25 A 2014-02-07 58.46 59.465 58.13 59.42 1975290 0.019385829473323086 58.10857142857144 58.56642857142856 58.586153846153856 0.0208855517672428 26 A 2014-02-10 59.27 59.44 58.29 59.01 1760468 -0.006900033658700836 58.03714285714286 58.434999999999995 58.60185185185186 0.020907172026060933 27 A 2014-02-11 59.0 60.0 58.88 59.73 2148202 0.012201321809862716 58.26285714285715 58.349285714285706 58.642142857142865 0.021239272852348213 28 A 2014-02-12 60.0 60.46 59.67 59.89 2347270 0.0026787209107651715 58.79714285714285 58.3792857142857